In [ ]:
"""
Please save notebooks with important results to your own folder in JupyterHub.
See README for usage instructions:
https://git.zooxlabs.com/zooxco/driving/tree/master/mined_metric/jupyter/README.md
"""
from mined_metric.jupyter.utils.data_access_util import get_experiment_data, chum_summary_stats
import urllib.parse

EXPERIMENT_ID = "EXPERIMENT_ID_PLACEHOLDER"

In [ ]:
# Retrieve all experiment data and metadata
exp_data = get_experiment_data(EXPERIMENT_ID)
if "exception" in exp_data:
    print("Invalid data is returned: %s" % exp_data["exception"])

In [ ]:
print("Copy and paste special (seperate columns by comma) the below into a google sheet for easy analysis:")
print("\n")
print("Original Chum,Converted Chum,Argus Link,Trajectory Metric Name,Total Mean Error,Worst Agent,2nd Worst,3rd Worst,Total Vehicles,Percent Moving Vehicles,Mean Driven Distance,Mean Fraction Missing Time,Notes")
for d in exp_data["meta"]:
    uri = d["chum_uri"]
    quoted_uri = "\"" + str(uri) + "\""
    if "sim_failed" in d:
        # If the sim crashes or has a monitor we don't get data or a synthetic chum uri
        print(quoted_uri + ",,,,,,,SIM_FAILURE")
        continue
    input_chum_uri= d["input_chum_uri"]
    quoted_input_chum_uri= "\"" + input_chum_uri + "\""
    chum_uri_argus_link = "\"argus.zooxlabs.com/uri?primaryUri={}".format(urllib.parse.quote(uri)) \
                          + "&comparisonUri={}".format(urllib.parse.quote(input_chum_uri)) \
                          + "&primaryNickname=Converted&comparisonNickname=Original\""
    
    
    for traj_metric_name in {"all", "car", "bicyclist", "pedestrian", "vehicles"}:
        if (traj_metric_name + "_number_of_samples") not in d:
            continue
        
        if d[traj_metric_name + "_number_of_samples"] is 0:
            # No agents
            print(quoted_input_chum_uri + "," + quoted_uri + "," + chum_uri_argus_link + "," + traj_metric_name + ",0,0,0,0,0,0,0,0,NO_AGENTS")
            continue
        # Sort agents by worst mean dist error
        list_of_agents = d[traj_metric_name + "_agent_errors"]
            
        agent_dict = {}
        for agent in list_of_agents:
            agent_dict[agent["track_id"]] = agent["mean_dist_error"]
        sorted_agents = sorted(agent_dict.items(), key=lambda x: x[1], reverse=True)
        
        # Format sorted agents
        top_three_agents=""
        cnt=0
        for agent in sorted_agents:
            if cnt > 2:
                continue
            top_three_agents+=str(agent[0])+": "+str(agent[1])+","
            cnt+=1

        # Scenario metrics
        converted_car_stats = d["converted_car_statistics"]
        scenario_metrics = str(converted_car_stats["number_of_agents"]) + "," + str(converted_car_stats["fraction_of_agents_moving"]) + "," + str(converted_car_stats["mean_distance_travelled"])
        print(quoted_input_chum_uri + "," + quoted_uri + "," + chum_uri_argus_link + "," + traj_metric_name + ","+str(d[traj_metric_name + "_mean_dist_error"]) + "," + top_three_agents + scenario_metrics + "," + str(d[traj_metric_name + "_mean_fraction_missing_time"]))
        print("\n")